# Surface Photometry Lab

The code below will fit elliptical apertures to astronomical images. Hold down the shift key and press Enter to run the code block below: it will load the Python libraries we need for this task. The grey brackets to the left of the code block will turn into an asterisk while the code is running, then turn to a sequence number when it finishes.

As you work through the lab, this is how you will run code blocks -- holding down Shift and pressing Enter. For some of them (particularly the ones that involve more math), you may have to wait a few moments for them to run. Just wait until the asterisk in the brackets turns to a sequence number.

In [ ]:
import numpy as np
from astropy.utils.data import download_file
from photutils.aperture import EllipticalAperture
from photutils.isophote import Ellipse
from photutils.isophote import EllipseGeometry
from astropy.io import fits
import matplotlib.pyplot as plt
from matplotlib.colors import LogNorm
import altair as alt
import pandas as pd

After we load in the necessary Python Packages (above), we need to load the image. The code below downloads the file from my webspace into a temprorary directory. The "cache=True" line ensures that the image doesn't have to be re-downloaded if you run the code multiple times. Make sure that you only download one image at a time by uncommenting the code lines, since only the most recent one will be remembered (or, alternately, change the variable names to load both at once). A number sign (a.k.a. hash) at the start of the line "comments" a line of code and ensures it doesn't run. Below, the image named 'ngc7817_i_sdss.fits' is commented out, so the image of NGC 5831 will load. 

In [ ]:
image_name='ngc5831_i_sdss.fits'
#image_name='ngc7817_i_sdss.fits'

file_name=download_file('http://faculty.bennington.edu/~hcrowl/'+image_name, cache=True)

In [ ]:
fits_image = fits.open(file_name)

In [ ]:
fits_image.info()

In the most general case, a fits image can have many layers. These can represent different wavelength bands (usually SDSS images have 5 layers for each of the 5 SDSS filters) or observations at different times or even different spectral channels (this last one is common in Radio/mm/sub-mm data). 

The fits images for this lab, however, have been edited to only have a single layer -- the 0th layer. As such, when we reference the data, we will put a [0] at the end of the variable name. 

We can read the header (the text at the beginning of the fits image that has information about the observations):

In [ ]:
fits_image[0].header

The header has information about the image. One thing we will need to know is the "pixel scale." This is a measurement of how angular size (e.g. arcseconds) corelate with pixels. The pixel scale *in degrees* is given in the CD1_1 and CD2_2 header values. What is the "pixel scale" of this image? That is, how many arcseconds coorespond to one pixel? *Important: The pixel scale here is given in degrees, so you'll need to multiply by the number of arcseconds in a degree to get the answer in arcseconds.*

**Make sure to record your answer somewhere, since you'll need it for later.**


Next, let's look at the actual image we've loaded. The data are just an array of numbers (that represent the brightness at each pixel level).

In [ ]:
fits_image[0].data

So, this is a little interesting, but it probably is better to actually display the image. We're going to use matplotlib's plotting package to do this. 

The first line sets the size of the image, the second tells it what data to display, how to do the color map ("cmap='gray'") and how to normalize the image (including the range of brightnesses to display). Because many astronomical images are high dynamic range images (i.e. a large range of brightnesses represented), we often display them with a "log stretch," which allows you to see the bright things and faint things at the same time. Finally, the last line displays the color bar on the right hand side. 

In [ ]:
plt.figure(figsize=(15,15))
plt.imshow(abs(fits_image[0].data), cmap='gray', norm=LogNorm(vmin=1E-3,vmax=300), origin='lower')
plt.colorbar()

Using what you wrote down from your work in DS9, adjust the variables in the code block below to reflect your first estimate for each of the following values:
- x0 is the pixel location of the center of the galaxy along the x-axis
- y0 is the pixel location of the center of the galaxy along the y-axis
- sma is the initial size of the semi-major axis for your first isophote -- ideally, this should represent a distance approximately halfway out in the galaxy (note this is probably the least important parameter).
- eps is the elipticity of the first isophote. 0 is round and 1 is completely flat.
- pa is a measure of the position angle. EllipseGeometry expects this in units of radians, so note that, while the input in the text box is in degrees, when I input into EllipseGeometry, I multiply by $\frac{\pi}{180}$.

These are the parameters that we have to feed in to EllipseGeometry at the start. Note that these don't need to be perfectly accurate, but the better job you do early on, the better the fit will be.

In [ ]:
x0 = 0
y0 = 0
sma = 0
eps = 0
pa = 0  #in degrees

In [ ]:
geometry = EllipseGeometry(x0=x0, y0=y0, sma=sma, eps=eps, pa=pa*np.pi/180.)

Next, we need to define the aperture (using the geometry we set up above) and plot that first isophote.

In [ ]:
aper=EllipticalAperture((geometry.x0, geometry.y0),geometry.sma,geometry.sma*(1-geometry.eps),geometry.pa)

plt.figure(figsize=(15,15))
plt.imshow(abs(fits_image[0].data), cmap='gray', norm=LogNorm(vmin=1E-3,vmax=200), origin='lower')
plt.colorbar()
aper.plot(color='red')

Does that look good? Does it match what you expected? If not, go up and tweak the parameters that you put in for EllipseGeometry and re-run the code blocks between there and here.

Once you are satisfied with your first ellipse, we can now create an object that we'll fit over -- the ellipse object.

In [ ]:
ellipse = Ellipse(fits_image[0].data,geometry)

Next we fit ellipses to the image, using the geometry we defined above. Note that, after this runs, we immediately convert it into a Pandas Dataframe which is, in general, a nicer format to work with. This next step may take a little while to run, since it's doing some fairly involved math to calculate all the isophotes. 

In [ ]:
isolist = ellipse.fit_image()
isodf=isolist.to_table(columns='all').to_pandas()

Next, we build a "model" of the galaxy's light using these ellipses. This "model" is a fake image that represents what the galaxy would look like if our model were a perfect fit to the true galaxy light. We also calculate the "residuals" -- how different the true galaxy light profile is from our model light profile. This will also probably take a little while to run. 

In [ ]:
from photutils.isophote import build_ellipse_model
model_image = build_ellipse_model(fits_image[0].data.shape, isolist)
residual = fits_image[0].data - model_image

Now, let's plot all of these things. 

In [ ]:
fig, (ax1, ax2, ax3) = plt.subplots(figsize=(28, 10), nrows=1, ncols=3)
fig.subplots_adjust(left=0.04, right=0.98, bottom=0.02, top=0.98)
ax1.imshow(abs(fits_image[0].data), origin='lower', norm=LogNorm(vmin=1E-3,vmax=200))
ax1.set_title('Data')

smas = np.linspace(10, 150, 50)
for sma in smas:
    iso = isolist.get_closest(sma)
    x, y, = iso.sampled_coordinates()
    ax1.plot(x, y, color='white')

ax2.imshow(abs(model_image), origin='lower', norm=LogNorm(vmin=1E-3,vmax=200))
ax2.set_title('Ellipse Model')

ax3.imshow(abs(residual), origin='lower', norm=LogNorm(vmin=1E-3,vmax=200))
ax3.set_title('Residual')

So, from left to right, that is the original Data, with isophotes plotted over the top, the ellipse model, and the "residuals" -- basically how different the real data are from the ellipse model. Does that look like the data are well-fit by the ellipse model? If so, move on. If not, go up and re-adjust the parameters for EllipseGeometry and re-run the code blocks. 

Next, let's look at the table with all the fit parameters in it. 

In [ ]:
isodf

Look at the DataFrame above. What do each of the columns mean? Write down the description in your lab (you're welcome to Google the names, which may help). 

Next, let's make a bunch of plots that show how relevant parameter change with radius. 

In [ ]:
intens = alt.Chart(isodf).mark_circle().encode(x='sma',y='intens').properties(width=400,height=400).interactive()
ellip = alt.Chart(isodf).mark_circle().encode(x='sma',y='ellipticity').properties(width=400,height=400).interactive()
pa = alt.Chart(isodf).mark_circle().encode(x='sma',y='pa').properties(width=400,height=400).interactive()
grad = alt.Chart(isodf).mark_circle().encode(x='sma',y='grad').properties(width=400,height=400).interactive()

(intens|ellip)&(pa|grad)

Finally, we'll write the isophote data to a csv file that you can use to make figures in other plotting packages (or, if you feel comfortable with Python, you can make those plots right here). 

In [ ]:
isodf.to_csv(image_name+'.csv')